## Round 1 
* Updating existing charts made by Tiffany. https://gtfs-digest--cal-itp-data-analyses.netlify.app/
* cd rt_segment_speeds && pip install altair_transform && pip install -r requirements.txt && cd ../_shared_utils && make setup_env

Links
* https://github.com/cal-itp/data-analyses/issues/1059
* https://docs.google.com/document/d/1I1WiqlmU06W6iLCi7cZQrOCLILkrEfABEkcU0Jys7f0/edit
* https://route-speeds--cal-itp-data-analyses.netlify.app/name_bay-area-511-muni-schedule/0__report__name_bay-area-511-muni-schedule
* https://posit-dev.github.io/great-tables/get-started/nanoplots.html
* https://docs.pola.rs/py-polars/html/reference/api/polars.from_pandas.html
* https://github.com/cal-itp/data-analyses/blob/main/rt_segment_speeds/_rt_scheduled_utils.py
* https://github.com/cal-itp/data-analyses/blob/main/rt_segment_speeds/_threshold_utils.py

In [1]:
import _report_utils
import _section2_utils as section2
import altair as alt
import calitp_data_analysis.magics
import geopandas as gpd
import great_tables as gt
import pandas as pd
from calitp_data_analysis import calitp_color_palette as cp
from great_tables import md
from IPython.display import HTML, Markdown, display
from segment_speed_utils.project_vars import RT_SCHED_GCS, SCHED_GCS
from shared_utils import catalog_utils, rt_dates, rt_utils

alt.renderers.enable("html")
alt.data_transformers.enable("default", max_rows=None)
from typing import List, Union

from altair_transform.extract import extract_transform
from altair_transform.transform import visit
from altair_transform.utils import to_dataframe

In [2]:
pd.options.display.max_columns = 100
pd.options.display.float_format = "{:.2f}".format
pd.set_option("display.max_rows", None)
pd.set_option("display.max_colwidth", None)

In [3]:
GTFS_DATA_DICT = catalog_utils.get_catalog("gtfs_analytics_data")
import yaml

with open("readable.yml") as f:
    readable_dict = yaml.safe_load(f)

In [4]:
org_name = "City of Fairfield"

In [5]:
# Set drop down menu to be on the upper right
display(
    HTML(
        """
<style>
form.vega-bindings {
  position: absolute;
  right: 0px;
  top: 0px;
}
</style>
"""
    )
)

### Original File 

In [6]:
schd_vp_url = f"{GTFS_DATA_DICT.digest_tables.dir}{GTFS_DATA_DICT.digest_tables.route_schedule_vp}.parquet"

In [7]:
og = pd.read_parquet(schd_vp_url)

In [8]:
og.columns

Index(['schedule_gtfs_dataset_key', 'direction_id', 'time_period',
       'avg_scheduled_service_minutes', 'avg_stop_miles', 'n_scheduled_trips',
       'frequency', 'is_express', 'is_rapid', 'is_rail', 'is_coverage',
       'is_downtown_local', 'is_local', 'service_date', 'typology',
       'minutes_atleast1_vp', 'minutes_atleast2_vp',
       'total_rt_service_minutes', 'total_scheduled_service_minutes',
       'total_vp', 'vp_in_shape', 'is_early', 'is_ontime', 'is_late',
       'n_vp_trips', 'vp_per_minute', 'pct_in_shape',
       'pct_rt_journey_atleast1_vp', 'pct_rt_journey_atleast2_vp',
       'pct_sched_journey_atleast1_vp', 'pct_sched_journey_atleast2_vp',
       'rt_sched_journey_ratio', 'avg_rt_service_minutes', 'sched_rt_category',
       'speed_mph', 'name', 'route_long_name', 'route_short_name',
       'route_combined_name', 'route_id', 'schedule_source_record_id',
       'base64_url', 'organization_source_record_id', 'organization_name',
       'caltrans_district'],
     

### Checkout Duplicates

In [9]:
df = section2.load_schedule_vp_metrics(org_name)

In [10]:
all_day = df.loc[df["Period"] == "all_day"]

### One Route

In [11]:
# one_route = df.loc[df["Route"] == '43 MASONIC']

In [12]:
# one_route.shape

In [13]:
# one_route_all_day = one_route.loc[one_route["Period"] == "all_day"]

In [14]:
# one_route_all_day["Route"].values[0]

#### Explanation Charts

In [15]:
def divider_chart(df: pd.DataFrame, text):
    df = df.head(1)
    # Create a text chart using Altair
    chart = (
        alt.Chart(df)
        .mark_text(
            align="center",
            baseline="middle",
            fontSize=12,
            text=text,
        )
        .properties(width=500, height=100)
    )

    return chart

In [16]:
divider_chart(df, "The charts below describe the quality of riding this route.")

alt.Chart(...)

#### Cleaning up Code

In [17]:
def set_y_axis(df, y_col):
    if "%" in y_col:
        max_y = 100

    elif "VP" in y_col:
        max_y = 3
    elif "Minute" in y_col:
        max_y = round(df[y_col].max())
    else:
        max_y = round(df[y_col].max(), -1) + 5
    return max_y

#### Avg Scheduled Minutes (Done)
* How come the average_scheduled_minutes is a lot shorter than total_rt_service_minutes and total_scheduled_service_minutes?
* Kind of a boring chart? Should compare actual run time compared to service minutes?

In [18]:
def grouped_bar_chart(
    df: pd.DataFrame,
    color_col: str,
    y_col: str,
    offset_col: str,
    title: str,
    subtitle: str,
):
    tooltip_cols = [
        "Direction",
        "Period",
        "Route",
        "Organization",
        "Date",
        color_col,
        y_col,
    ]

    if len(df) == 0:
        text_chart = section2.create_data_unavailable_chart()
        return text_chart
    else:
        df = section2.clean_data_charts(df, y_col)
        chart = (
            alt.Chart(df)
            .mark_bar(size=10)
            .encode(
                x=alt.X(
                    "yearmonthdate(Date):O",
                    title=["Grouped by Direction ID", "Date"],
                    axis=alt.Axis(labelAngle=-45, format="%b %Y"),
                ),
                y=alt.Y(f"{y_col}:Q", title=_report_utils.labeling(y_col)),
                xOffset=alt.X(
                    f"{offset_col}:N", title=_report_utils.labeling(offset_col)
                ),
                color=alt.Color(
                    f"{color_col}:N",
                    title=_report_utils.labeling(color_col),
                    scale=alt.Scale(
                        range=_report_utils.red_green_yellow,
                    ),
                ),
                tooltip=tooltip_cols,
            )
        )
        chart = (chart).properties(
            title={
                "text": [title],
                "subtitle": [subtitle],
            },
            width=500,
            height=300,
        )

        return chart

In [19]:
grouped_bar_chart(
    df=all_day,
    color_col="Direction",
    y_col="Average Scheduled Service (trip minutes)",
    offset_col="Direction",
    title=readable_dict["avg_scheduled_min_graph"]["title"],
    subtitle=readable_dict["avg_scheduled_min_graph"]["subtitle"],
)

/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:281: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Period"] = df["Period"].str.replace("_", " ").str.title()
/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:283: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[y_col] = df[y_col].fillna(0).astype(int)
/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:284: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_in

alt.Chart(...)

#### Timeliness #2 (Done)

In [20]:
def timeliness_trips(df: pd.DataFrame):
    df = df.loc[df["Period"] != "All Day"]
    df = df.loc[df["Period"] != "all_day"]
    to_keep = [
        "Date",
        "Organization",
        "Direction",
        "Period",
        "Route",
        "# Early Arrival Trips",
        "# On-Time Trips",
        "# Late Trips",
        "# Trips with VP",
    ]
    df = df.loc[df["Period"] != "All Day"]
    df2 = df[to_keep]

    melted_df = df2.melt(
        id_vars=[
            "Date",
            "Organization",
            "Route",
            "Period",
            "Direction",
        ],
        value_vars=[
            "# Early Arrival Trips",
            "# On-Time Trips",
            "# Late Trips",
        ],
    )
    return melted_df

In [21]:
timeliness_test = timeliness_trips(df)

In [22]:
timeliness_test

Date       Organization  \
0   2023-03-15  City of Fairfield   
1   2023-04-12  City of Fairfield   
2   2023-05-17  City of Fairfield   
3   2023-06-14  City of Fairfield   
4   2023-07-12  City of Fairfield   
5   2023-08-15  City of Fairfield   
6   2023-09-13  City of Fairfield   
7   2023-10-11  City of Fairfield   
8   2023-11-15  City of Fairfield   
9   2023-12-13  City of Fairfield   
10  2024-01-17  City of Fairfield   
11  2024-02-14  City of Fairfield   
12  2024-03-13  City of Fairfield   
13  2024-04-17  City of Fairfield   
14  2023-03-15  City of Fairfield   
15  2023-04-12  City of Fairfield   
16  2023-05-17  City of Fairfield   
17  2023-06-14  City of Fairfield   
18  2023-07-12  City of Fairfield   
19  2023-08-15  City of Fairfield   
20  2023-09-13  City of Fairfield   
21  2023-10-11  City of Fairfield   
22  2023-11-15  City of Fairfield   
23  2023-12-13  City of Fairfield   
24  2024-01-17  City of Fairfield   
25  2024-02-14  City of Fairfield   
26  2024-03-13  City of Fairfield   
27  2024-04-17  City of Fairfield   
28  2023-03-15  City of Fairfield   
29  2023-04-12  City of Fairfield   
30  2023-05-17  City of Fairfield   
31  2023-06-14  City of Fairfield   
32  2023-07-12  City of Fairfield   
33  2023-08-15  City of Fairfield   
34  2023-09-13  City of Fairfield   
35  2023-10-11  City of Fairfield   
36  2023-11-15  City of Fairfield   
37  2023-12-13  City of Fairfield   
38  2024-01-17  City of Fairfield   
39  2024-02-14  City of Fairfield   
40  2024-03-13  City of Fairfield   
41  2024-04-17  City of Fairfield   
42  2023-03-15  City of Fairfield   
43  2023-04-12  City of Fairfield   
44  2023-05-17  City of Fairfield   
45  2023-06-14  City of Fairfield   
46  2023-07-12  City of Fairfield   
47  2023-08-15  City of Fairfield   
48  2023-09-13  City of Fairfield   
49  2023-10-11  City of Fairfield   
50  2023-11-15  City of Fairfield   
51  2023-12-13  City of Fairfield   
52  2024-01-17  City of Fairfield   
53  2024-02-14  City of Fairfield   
54  2024-03-13  City of Fairfield   
55  2024-04-17  City of Fairfield   
56  2023-03-15  City of Fairfield   
57  2023-04-12  City of Fairfield   
58  2023-05-17  City of Fairfield   
59  2023-06-14  City of Fairfield   
60  2023-07-12  City of Fairfield   
61  2023-08-15  City of Fairfield   
62  2023-03-15  City of Fairfield   
63  2023-04-12  City of Fairfield   
64  2023-05-17  City of Fairfield   
65  2023-06-14  City of Fairfield   
66  2023-07-12  City of Fairfield   
67  2023-08-15  City of Fairfield   
68  2023-03-15  City of Fairfield   
69  2023-04-12  City of Fairfield   
70  2023-05-17  City of Fairfield   
71  2023-06-14  City of Fairfield   
72  2023-07-12  City of Fairfield   
73  2023-08-15  City of Fairfield   
74  2023-03-15  City of Fairfield   
75  2023-04-12  City of Fairfield   
76  2023-05-17  City of Fairfield   
77  2023-06-14  City of Fairfield   
78  2023-07-12  City of Fairfield   
79  2023-08-15  City of Fairfield   
80  2023-03-15  City of Fairfield   
81  2023-04-12  City of Fairfield   
82  2023-05-17  City of Fairfield   
83  2023-06-14  City of Fairfield   
84  2023-07-12  City of Fairfield   
85  2023-08-15  City of Fairfield   
86  2023-09-13  City of Fairfield   
87  2023-10-11  City of Fairfield   
88  2023-11-15  City of Fairfield   
89  2023-12-13  City of Fairfield   
90  2024-01-17  City of Fairfield   
91  2024-02-14  City of Fairfield   
92  2024-03-13  City of Fairfield   
93  2024-04-17  City of Fairfield   
94  2023-03-15  City of Fairfield   
95  2023-04-12  City of Fairfield   
96  2023-05-17  City of Fairfield   
97  2023-06-14  City of Fairfield   
98  2023-07-12  City of Fairfield   
99  2023-08-15  City of Fairfield   
100 2023-09-13  City of Fairfield   
101 2023-10-11  City of Fairfield   
102 2023-11-15  City of Fairfield   
103 2023-12-13  City of Fairfield   
104 2024-01-17  City of Fairfield   
105 2024-02-14  City of Fairfield   
106 2024-03-13  City of Fairfield   
107 2024-04-17

In [23]:
def base_facet_chart(
    df: pd.DataFrame,
    y_col: str,
    color_col: str,
    facet_col: str,
    title: str,
    subtitle: str,
):
    tooltip_cols = [
        "Direction",
        "Period",
        "Route",
        "Organization",
        "Date",
        y_col,
        color_col,
    ]

    if len(df) == 0:
        text_chart = section2.create_data_unavailable_chart()
        return text_chart
    else:
        max_y = set_y_axis(df, y_col)
        df = section2.clean_data_charts(df, y_col)
        chart = (
            (
                alt.Chart(df)
                .mark_bar(size=15, clip=True)
                .encode(
                    x=alt.X(
                        "yearmonthdate(Date):O",
                        title=["Date"],
                        axis=alt.Axis(labelAngle=-45, format="%b %Y"),
                    ),
                    y=alt.Y(
                        f"{y_col}:Q",
                        title=_report_utils.labeling(y_col),
                        scale=alt.Scale(domain=[0, max_y]),
                    ),
                    color=alt.Color(
                        f"{color_col}:N",
                        title=_report_utils.labeling(color_col),
                        scale=alt.Scale(range=_report_utils.red_green_yellow),
                    ),
                    tooltip=tooltip_cols,
                )
            )
            .facet(
                column=alt.Column(
                    f"{facet_col}:N",
                )
            )
            .properties(
                title={
                    "text": title,
                    "subtitle": subtitle,
                }
            )
        )
        return chart

In [24]:
base_facet_chart(
    timeliness_test.loc[timeliness_test["Direction"] == 1],
    "value",
    "variable",
    "Period",
    readable_dict["timeliness_trips_dir_1_graph"]["title"],
    readable_dict["timeliness_trips_dir_0_graph"]["subtitle"],
)

/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:281: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Period"] = df["Period"].str.replace("_", " ").str.title()
/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:283: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[y_col] = df[y_col].fillna(0).astype(int)
/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:284: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_in

alt.FacetChart(...)

In [25]:
base_facet_chart(
    timeliness_test.loc[timeliness_test["Direction"] == 0],
    "value",
    "variable",
    "Period",
    readable_dict["timeliness_trips_dir_0_graph"]["title"],
    readable_dict["timeliness_trips_dir_0_graph"]["subtitle"],
)

/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:281: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Period"] = df["Period"].str.replace("_", " ").str.title()
/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:283: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[y_col] = df[y_col].fillna(0).astype(int)
/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:284: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_in

alt.FacetChart(...)

#### Frequency (Done)
* Maybe shouldn't be a chart since there doesn't seem to be a lot of data for this across a lot of the routes?
* What does frequency mean?
* Simplify down to not take direction_id into consideration?

In [26]:
def frequency_chart(df: pd.DataFrame):
    if len(df) == 0:
        text_chart = create_data_unavailable_chart()
        return text_chart

    else:
        df["Frequency in Minutes"] = (
            "A trip going this direction comes every "
            + df.frequency_in_minutes.astype(int).astype(str)
            + " minutes"
        )
        chart = (
            alt.Chart(df)
            .properties(width=180, height=alt.Step(10))
            .mark_bar()
            .encode(
                alt.Y(
                    "yearmonthdate(Date):O",
                    title="Date",
                    axis=alt.Axis(format="%b %Y"),
                ),
                alt.X(
                    "frequency_in_minutes:Q",
                    title=_report_utils.labeling("frequency_in_minutes"),
                    axis=None,
                ),
                alt.Color(
                    "frequency_in_minutes:Q",
                    scale=alt.Scale(range=_report_utils.green_red_yellow),
                ).title(_report_utils.labeling("frequency_in_minutes")),
                alt.Row("Period:N")
                .title(_report_utils.labeling("Period"))
                .header(labelAngle=0),
                alt.Column("Direction:N").title(_report_utils.labeling("Direction")),
                tooltip=["Date", "Frequency in Minutes", "Period", "Direction"],
            )
        )
        chart = chart.properties(
            title={
                "text": readable_dict["frequency_graph"]["title"],
                "subtitle": readable_dict["frequency_graph"]["subtitle"],
            }
        )
        return chart

In [27]:
frequency_chart(df)

alt.Chart(...)

In [28]:
source = pd.DataFrame(
    [
        {"a": "a1", "b": "b1", "c": "x", "p": "0.14"},
        {"a": "a1", "b": "b1", "c": "y", "p": "0.60"},
        {"a": "a1", "b": "b1", "c": "z", "p": "0.03"},
        {"a": "a1", "b": "b2", "c": "x", "p": "0.80"},
        {"a": "a1", "b": "b2", "c": "y", "p": "0.38"},
        {"a": "a1", "b": "b2", "c": "z", "p": "0.55"},
        {"a": "a1", "b": "b3", "c": "x", "p": "0.11"},
        {"a": "a1", "b": "b3", "c": "y", "p": "0.58"},
        {"a": "a1", "b": "b3", "c": "z", "p": "0.79"},
        {"a": "a2", "b": "b1", "c": "x", "p": "0.83"},
        {"a": "a2", "b": "b1", "c": "y", "p": "0.87"},
        {"a": "a2", "b": "b1", "c": "z", "p": "0.67"},
        {"a": "a2", "b": "b2", "c": "x", "p": "0.97"},
        {"a": "a2", "b": "b2", "c": "y", "p": "0.84"},
        {"a": "a2", "b": "b2", "c": "z", "p": "0.90"},
        {"a": "a2", "b": "b3", "c": "x", "p": "0.74"},
        {"a": "a2", "b": "b3", "c": "y", "p": "0.64"},
        {"a": "a2", "b": "b3", "c": "z", "p": "0.19"},
        {"a": "a3", "b": "b1", "c": "x", "p": "0.57"},
        {"a": "a3", "b": "b1", "c": "y", "p": "0.35"},
        {"a": "a3", "b": "b1", "c": "z", "p": "0.49"},
        {"a": "a3", "b": "b2", "c": "x", "p": "0.91"},
        {"a": "a3", "b": "b2", "c": "y", "p": "0.38"},
        {"a": "a3", "b": "b2", "c": "z", "p": "0.91"},
        {"a": "a3", "b": "b3", "c": "x", "p": "0.99"},
        {"a": "a3", "b": "b3", "c": "y", "p": "0.80"},
        {"a": "a3", "b": "b3", "c": "z", "p": "0.37"},
    ]
)

alt.Chart(source, width=60, height=alt.Step(8)).mark_bar().encode(
    alt.Y("c:N").axis(None),
    alt.X("p:Q").title(None).axis(format="%"),
    alt.Color("c:N").title("settings").legend(orient="bottom", titleOrient="left"),
    alt.Row("a:N").title("Factor A").header(labelAngle=0),
    alt.Column("b:N").title("Factor B"),
)

alt.Chart(...)

#### Speed MPH (Done)
* Needs a different type of chart.

In [29]:
def base_facet_line(
    df: pd.DataFrame, y_col: str, title: str, subtitle: str
) -> alt.Chart:
    if len(df) == 0:
        text_chart = section2.create_data_unavailable_chart()
        return text_chart
    else:
        max_y = set_y_axis(df, y_col)

        df = section2.clean_data_charts(df, y_col)
        tooltip_cols = [
            "Route",
            "Direction",
            "Period",
            f"{y_col}_str",
        ]

        chart = (
            alt.Chart(df)
            .mark_line(size=5)
            .encode(
                x=alt.X(
                    "yearmonthdate(Date):O",
                    title="Date",
                    axis=alt.Axis(labelAngle=-45, format="%b %Y"),
                ),
                y=alt.Y(
                    f"{y_col}:Q",
                    title=_report_utils.labeling(y_col),
                    scale=alt.Scale(domain=[0, max_y]),
                ),
                color=alt.Color(
                    "Period:N",
                    title=_report_utils.labeling("Period"),
                    scale=alt.Scale(range=_report_utils.red_green_yellow),
                ),
                tooltip=tooltip_cols,
            )
        )

        chart = chart.properties(width=250, height=300)
        chart = chart.facet(
            column=alt.Column("Direction:N", title=_report_utils.labeling("Direction")),
        ).properties(
            title={
                "text": [title],
                "subtitle": [subtitle],
            }
        )
        return chart

In [30]:
base_facet_line(
    df,
    "Speed (MPH)",
    readable_dict["speed_graph"]["title"],
    readable_dict["speed_graph"]["subtitle"],
)

alt.FacetChart(...)

#### VP per Minute 

In [31]:
def base_facet_with_ruler_chart(
    df: pd.DataFrame,
    y_col: str,
    ruler_col: str,
    title: str,
    subtitle: str,
):
    tooltip_cols = [
        "Direction",
        "Period",
        "Route",
        "Organization",
        "Date",
        y_col,
    ]

    if len(df) == 0:
        text_chart = section2.create_data_unavailable_chart()
        return text_chart
    else:
        max_y = set_y_axis(df, y_col)
        ruler = (
            alt.Chart(df)
            .mark_rule(color="red", strokeDash=[10, 7])
            .encode(y=f"mean({ruler_col}):Q")
        )
        chart = (
            alt.Chart(df)
            .mark_bar(size=15, clip=True)
            .encode(
                x=alt.X(
                    "yearmonthdate(Date):O",
                    title=["Date"],
                    axis=alt.Axis(labelAngle=-45, format="%b %Y"),
                ),
                y=alt.Y(
                    f"{y_col}:Q",
                    title=_report_utils.labeling(y_col),
                    scale=alt.Scale(domain=[0, max_y]),
                ),
                color=alt.Color(
                    f"{y_col}:Q",
                    title=_report_utils.labeling(y_col),
                    scale=alt.Scale(range=_report_utils.red_green_yellow),
                ),
                tooltip=df[tooltip_cols].columns.tolist(),
            )
        )

        chart = chart + ruler
        chart = chart.facet(column=alt.Column("Direction:N",)).properties(
            title={
                "text": title,
                "subtitle": [subtitle],
            }
        )

        return chart

In [32]:
base_facet_with_ruler_chart(
    all_day,
    "Average VP per Minute",
    "ruler_for_vp_per_min",
    readable_dict["vp_per_min_graph"]["title"],
    readable_dict["vp_per_min_graph"]["subtitle"],
)

alt.FacetChart(...)

#### Spatial Accuracy (Done)
* Multiple it by 100? Should this be rounded or not?

In [33]:
base_facet_with_ruler_chart(
    all_day,
    "% VP within Scheduled Shape",
    "ruler_100_pct",
    readable_dict["spatial_accuracy_graph"]["title"],
    readable_dict["spatial_accuracy_graph"]["title"],
)

alt.FacetChart(...)

#### % RT journey with 1+/2+ vp (goal line = 100%) - use all_day, one chart shared for 1+ and 2+ (Done need subtitle)

In [34]:
def pct_vp_journey(df: pd.DataFrame, col1: str, col2: str) -> pd.DataFrame:
    to_keep = [
        "Date",
        "Organization",
        "Direction",
        col1,
        col2,
        "Route",
        "Period",
        "ruler_100_pct",
    ]
    df2 = df[to_keep]

    df3 = df2.melt(
        id_vars=[
            "Date",
            "Organization",
            "Route",
            "Direction",
            "Period",
            "ruler_100_pct",
        ],
        value_vars=[col1, col2],
    )

    df3 = df3.rename(
        columns={"variable": "Category", "value": "% of Actual Trip Minutes"}
    )
    return df3

In [35]:
rt_pct = pct_vp_journey(
    all_day,
    "% Actual Trip Minutes with 1+ VP per Minute",
    "% Actual Trip Minutes with 2+ VP per Minute",
)

In [36]:
def base_facet_circle(
    df: pd.DataFrame,
    y_col: str,
    color_col: str,
    ruler_col: str,
    title: str,
    subtitle: str,
) -> alt.Chart:

    tooltip_cols = [
        "Direction",
        "Period",
        "Route",
        "Date",
        f"{y_col}_str",
        color_col,
    ]

    if len(df) == 0:
        text_chart = section2.create_data_unavailable_chart()
        return text_chart
    else:
        max_y = set_y_axis(df, y_col)
        df = section2.clean_data_charts(df, y_col)
        ruler = (
            alt.Chart(df)
            .mark_rule(color="red", strokeDash=[10, 7])
            .encode(y=f"ruler_100_pct:Q")
        )

        chart = (
            alt.Chart(df)
            .mark_circle(size=150)
            .encode(
                x=alt.X(
                    "yearmonthdate(Date):O",
                    title="Date",
                    axis=alt.Axis(labelAngle=-45, format="%b %Y"),
                ),
                y=alt.Y(
                    f"{y_col}:Q",
                    title=_report_utils.labeling(y_col),
                    scale=alt.Scale(domain=[0, max_y]),
                ),
                color=alt.Color(
                    f"{color_col}:N",
                    title=_report_utils.labeling(color_col),
                    scale=alt.Scale(range=_report_utils.red_green_yellow),
                ),
                tooltip=tooltip_cols,
            )
        )

        chart = chart + ruler
        chart = chart.facet(
            column=alt.Column("Direction:N", title=_report_utils.labeling("Direction")),
        ).properties(
            title={
                "text": [title],
                "subtitle": [subtitle],
            }
        )
        return chart

In [37]:
base_facet_circle(
    rt_pct,
    "% of Actual Trip Minutes",
    "Category",
    "ruler_100_pct",
    readable_dict["rt_vp_per_min_graph"]["title"],
    readable_dict["rt_vp_per_min_graph"]["subtitle"],
)

alt.FacetChart(...)

#### Text

In [38]:
table_df = section2.route_stats(df)

In [39]:
def create_text_table(df: pd.DataFrame, direction: float):

    df = df.loc[df["Direction"] == direction].drop_duplicates().reset_index(drop=True)

    if len(df) == 0:
        text_chart = section2.create_data_unavailable_chart()
        return text_chart

    else:
        df2 = df.melt(
            id_vars=[
                "Route",
                "Direction",
            ],
            value_vars=[
                "Average Scheduled Service (Trip Minutes)",
                "Average Stop Distance (Miles)",
                "# Scheduled Trips",
                "Gtfs Availability",
                "Peak Avg Speed",
                "Peak Scheduled Trips",
                "Peak Hourly Freq",
                "Offpeak Avg Speed",
                "Offpeak Scheduled Trips",
                "Trips Per Hour",
            ],
        )
        # Create a decoy column to center all the text
        df2["Zero"] = 0

        df2["combo_col"] = df2.variable.astype(str) + ": " + df2.value.astype(str)
        df2.combo_col = df2.combo_col.str.replace(
            "schedule_and_vp", "Schedule and Realtime Data"
        )
        text_chart = (
            alt.Chart(df2)
            .mark_text()
            .encode(x=alt.X("Zero:Q", axis=None), y=alt.Y("combo_col", axis=None))
        )

        text_chart = text_chart.encode(text="combo_col:N").properties(
            title=f"Route Statistics for Direction {direction}",
            width=500,
            height=300,
        )
        return text_chart

In [40]:
create_text_table(table_df, 0)

alt.Chart(...)

#### Putting it all together

In [41]:
def filtered_route_test(
    df: pd.DataFrame,
) -> alt.Chart:
    """
    https://stackoverflow.com/questions/58919888/multiple-selections-in-altair
    """
    # Create dropdown
    routes_list = df["Route"].unique().tolist()

    route_dropdown = alt.binding_select(
        options=routes_list,
        name="Routes",
    )
    # Column that controls the bar charts
    route_selector = alt.selection_point(
        fields=["Route"],
        bind=route_dropdown,
    )

    # Filter for only rows categorized as found in schedule and vp and all_day
    all_day = df.loc[df["Period"] == "All Day"].reset_index(drop=True)

    # Create route stats table for the text tables
    route_stats_df = section2.route_stats(df)

    # Manipulate the df for some of the metrics
    timeliness_df = timeliness_trips(df)

    rt_journey_vp = pct_vp_journey(
        all_day,
        "% Actual Trip Minutes with 1+ VP per Minute",
        "% Actual Trip Minutes with 2+ VP per Minute",
    )
    sched_journey_vp = pct_vp_journey(
        all_day,
        "% Scheduled Trip Minutes with 1+ VP per Minute",
        "% Scheduled Trip Minutes with 2+ VP per Minute",
    )

    avg_scheduled_min_graph = (
        grouped_bar_chart(
            df=all_day,
            color_col="Direction",
            y_col="Average Scheduled Service (trip minutes)",
            offset_col="Direction",
            title=readable_dict["avg_scheduled_min_graph"]["title"],
            subtitle=readable_dict["avg_scheduled_min_graph"]["subtitle"],
        )
        .add_params(route_selector)
        .transform_filter(route_selector)
    )
    # display(avg_scheduled_min_graph)
    timeliness_trips_dir_0 = (
        (
            base_facet_chart(
                timeliness_df.loc[timeliness_df["Direction"] == 0],
                "value",
                "variable",
                "Period",
                readable_dict["timeliness_trips_dir_0_graph"]["title"],
                readable_dict["timeliness_trips_dir_0_graph"]["subtitle"],
            )
        )
        .add_params(route_selector)
        .transform_filter(route_selector)
    )
    # display(timeliness_trips_dir_0)
    timeliness_trips_dir_1 = (
        (
            base_facet_chart(
                timeliness_df.loc[timeliness_df["Direction"] == 1],
                "value",
                "variable",
                "Period",
                readable_dict["timeliness_trips_dir_1_graph"]["title"],
                readable_dict["timeliness_trips_dir_0_graph"]["subtitle"],
            )
        )
        .add_params(route_selector)
        .transform_filter(route_selector)
    )
    # display(timeliness_trips_dir_1)
    frequency_graph = (
        frequency_chart(df).add_params(route_selector).transform_filter(route_selector)
    )
    # display(frequency_graph)
    speed_graph = (
        base_facet_line(
            df,
            "Speed (MPH)",
            readable_dict["speed_graph"]["title"],
            readable_dict["speed_graph"]["subtitle"],
        )
        .add_params(route_selector)
        .transform_filter(route_selector)
    )
    # display(speed_graph)
    vp_per_min_graph = (
        (
            base_facet_with_ruler_chart(
                all_day,
                "Average VP per Minute",
                "ruler_for_vp_per_min",
                readable_dict["vp_per_min_graph"]["title"],
                readable_dict["vp_per_min_graph"]["subtitle"],
            )
        )
        .add_params(route_selector)
        .transform_filter(route_selector)
    )
    # display(vp_per_min_graph)
    rt_vp_per_min_graph = (
        base_facet_circle(
            rt_journey_vp,
            "% of Actual Trip Minutes",
            "Category",
            "ruler_100_pct",
            readable_dict["rt_vp_per_min_graph"]["title"],
            readable_dict["rt_vp_per_min_graph"]["subtitle"],
        )
        .add_params(route_selector)
        .transform_filter(route_selector)
    )
    # display(rt_vp_per_min_graph)
    sched_vp_per_min = (
        base_facet_circle(
            sched_journey_vp,
            "% of Actual Trip Minutes",
            "Category",
            "ruler_100_pct",
            readable_dict["sched_vp_per_min_graph"]["title"],
            readable_dict["rt_vp_per_min_graph"]["subtitle"],
        )
        .add_params(route_selector)
        .transform_filter(route_selector)
    )
    # display(sched_vp_per_min)
    spatial_accuracy = (
        base_facet_with_ruler_chart(
            all_day,
            "% VP within Scheduled Shape",
            "ruler_100_pct",
            readable_dict["spatial_accuracy_graph"]["title"],
            readable_dict["spatial_accuracy_graph"]["title"],
        )
        .add_params(route_selector)
        .transform_filter(route_selector)
    )
    # display(spatial_accuracy)
    text_dir0 = (
        (create_text_table(route_stats_df, 0))
        .add_params(route_selector)
        .transform_filter(route_selector)
    )
    # display(text_dir0)
    text_dir1 = (
        create_text_table(route_stats_df, 1)
        .add_params(route_selector)
        .transform_filter(route_selector)
    )
    # display(text_dir1)

    chart_list = [
        avg_scheduled_min_graph,
        timeliness_trips_dir_0,
        timeliness_trips_dir_1,
        frequency_graph,
        speed_graph,
        vp_per_min_graph,
        rt_vp_per_min_graph,
        sched_vp_per_min,
        spatial_accuracy,
        text_dir0,
        text_dir1,
    ]

    chart = alt.vconcat(*chart_list)

    return chart

In [42]:
filtered_route_test(df)

/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:281: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Period"] = df["Period"].str.replace("_", " ").str.title()
/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:283: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[y_col] = df[y_col].fillna(0).astype(int)
/home/jovyan/data-analyses/gtfs_digest/_section2_utils.py:284: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_in

alt.VConcatChart(...)